* 피처엔지니어링 통합본
* 생각한 피처와 참고한 커널 등 모든 피처에 대해 정리

# 사전작업

## 모듈 임포트

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import datetime
import seaborn as sns
import gc

In [2]:
import warnings
warnings.filterwarnings('ignore')

In [3]:
pd.set_option('display.max_columns', 400)

## 데이터 로드

In [6]:
path = '../data/'

In [7]:
train = pd.read_csv(path + 'train.csv')
test = pd.read_csv(path + 'test.csv')
history = pd.read_csv(path + 'historical_transactions.csv')
new_history = pd.read_csv(path + 'new_merchant_transactions.csv')
# merchant = pd.read_csv(path + 'merchants.csv')

In [8]:
debug = True

if debug:
    history = history[:10000]
    new_history = new_history[:10000]

## 데이터 크기 줄이기

In [55]:
def reduce_mem_usage(df, verbose=True):
    numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
    start_mem = df.memory_usage().sum() / 1024**2    
    for col in df.columns:
        col_type = df[col].dtypes
        if col_type in numerics:
            c_min = df[col].min()
            c_max = df[col].max()
            if str(col_type)[:3] == 'int':
                if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
                    df[col] = df[col].astype(np.int16)
                elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
                    df[col] = df[col].astype(np.int64)  
            else:
                if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)    
    end_mem = df.memory_usage().sum() / 1024**2
    if verbose: print('Mem. usage decreased to {:5.2f} Mb ({:.1f}% reduction)'.format(end_mem, 100 * (start_mem - end_mem) / start_mem))
    return df

In [110]:
for df in [train, test, history, new_history]:
    df = reduce_mem_usage(df)
    gc.collect()

Mem. usage decreased to  4.04 Mb (56.2% reduction)
Mem. usage decreased to  2.24 Mb (52.5% reduction)
Mem. usage decreased to  0.57 Mb (46.4% reduction)
Mem. usage decreased to  0.57 Mb (46.4% reduction)


# Feature Engineering

* 1) 단일 피처에서의 엔지니어링 (2월 3일)
* 2) 피처 사이의 엔지니어링 (2월 5일)

## 단일 피처 엔지니어링

### train & test

In [7]:
for df in [train, test]:
    # first_active_month
    df['first_active'] = pd.to_datetime(df['first_active_month'])
    df['first_active_year'] = df['first_active'].dt.year
    df['first_active_month'] = df['first_active'].dt.month
    df['first_active_quarter'] = df['first_active'].dt.quarter
    df['first_active_weekofyear'] = df['first_active'].dt.weekofyear
    df['first_active_dayofweek'] = df['first_active'].dt.dayofweek
    # 모든 데이터의 마지막 거래날짜가 2018년 4월 30일 23시 59분 59초
    df['first_active_elapsed_time_from_trade'] = (datetime.datetime(2018, 4, 30, 23, 59, 59) - df['first_active']).dt.days
    df['first_active_elapsed_time_from_today'] = (datetime.datetime.today() - df['first_active']).dt.days

* feature_1, feature_2, feature_3 추가 피처엔지니어링 필요

### history & new_history

#### util functions

In [14]:
from scipy import stats
def mode(x):
    return stats.mode(x)[0][0]

In [15]:
def null_cnt(x):
    return np.sum(x.isna() * 1)

In [16]:
def over_550(data):
    return len(data[data > 550])

In [76]:
def ref_date(data):
    ref_month = data.purchase_month - data.month_lag
    
    if ref_month % 12 == 0:
        ref_year = ref_month // 12 - 1
        ref_month = 12
        
    else:
        ref_year = ref_month // 12
        ref_month = ref_month % 12
        
    ref_year = data.purchase_year + ref_year
    return datetime.datetime(ref_year, ref_month, 1, 0, 0, 0)

#### 통합 전처리

In [77]:
for df in [history, new_history]:
    # fillna - category_3, merchant_id, category_2, installments, city_id, state_id
    df['category_2'].fillna(1.0,inplace=True)
    df['category_3'].fillna('A',inplace=True)
    df['merchant_id'].fillna(np.nan,inplace=True)
    df['installments'].replace(-1, np.nan,inplace=True)
    df['installments'].replace(999, np.nan,inplace=True)
    
    # label encoding
    df['authorized_flag'] = df['authorized_flag'].map({'Y':1, 'N':0})
    df['category_1'] = df['category_1'].map({'Y':1, 'N':0})
    df['category_3'] = df['category_3'].map({'A':0, 'B':1, 'C':2})
    
    # trim purchase amount
    df['purchase_amount_trim'] = df['purchase_amount'].apply(lambda x: min(x, 0.8))
    
    # purchase date
    df['purchase_date'] = pd.to_datetime(df['purchase_date'])
    df['purchase_year'] = df['purchase_date'].dt.year
    df['purchase_month'] = df['purchase_date'].dt.month
    df['purchase_day'] = df['purchase_date'].dt.day
    df['purchase_hour'] = df['purchase_date'].dt.hour
    df['purchase_dayofweek'] = df['purchase_date'].dt.dayofweek
    df['purchase_weekofyear'] = df['purchase_date'].dt.weekofyear
    df['purchase_weekend'] = (df['purchase_date'].dt.weekday >=5).astype(int)
    df['ref_date'] = df.apply(ref_date, axis = 1)

In [78]:
history

authorized_flag          card_id  city_id  category_1  installments  \
0                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
1                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
2                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
3                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
4                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
5                 NaN  C_ID_4e6213e9bc      333         NaN           0.0   
6                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
7                 NaN  C_ID_4e6213e9bc        3         NaN           0.0   
8                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
9                 NaN  C_ID_4e6213e9bc       88         NaN           0.0   
10                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
11                NaN  C_ID_4e6213e9bc       -1         NaN           0.0   
12                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
13                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
14                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
15                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
16                NaN  C_ID_4e6213e9bc       69         NaN           0.0   
17                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
18                NaN  C_ID_4e6213e9bc      233         NaN           0.0   
19                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
20                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
21                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
22                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
23                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
24                NaN  C_ID_4e6213e9bc        3         NaN           0.0   
25                NaN  C_ID_4e6213e9bc      333         NaN           0.0   
26                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
27                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
28                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
29                NaN  C_ID_4e6213e9bc       88         NaN           0.0   
...               ...              ...      ...         ...           ...   
9970              NaN  C_ID_2223b33279      200         NaN           0.0   
9971              NaN  C_ID_2223b33279      344         NaN           0.0   
9972              NaN  C_ID_2223b33279      344         NaN           0.0   
9973              NaN  C_ID_2223b33279      344         NaN           0.0   
9974              NaN  C_ID_2223b33279      344         NaN           0.0   
9975              NaN  C_ID_2223b33279      200         NaN           0.0   
9976              NaN  C_ID_2223b33279      344         NaN           0.0   
9977              NaN  C_ID_2223b33279      107         NaN           0.0   
9978              NaN  C_ID_2223b33279      344         NaN           0.0   
9979              NaN  C_ID_2223b33279      344         NaN           0.0   
9980              NaN  C_ID_2223b33279      200         NaN           0.0   
9981              NaN  C_ID_2223b33279      344         NaN           0.0   
9982              NaN  C_ID_2223b33279      344         NaN           0.0   
9983              NaN  C_ID_2223b33279       -1         NaN           1.0   
9984              NaN  C_ID_2223b33279      344         NaN           0.0   
9985              NaN  C_ID_2223b33279      331         NaN           0.0   
9986              NaN  C_ID_2223b33279      344         NaN           0.0   
9987              NaN  C_ID_2223b33279      344         NaN           0.0   
9988              NaN  C_ID_2223b33279      344         NaN           0.0   
9989              NaN  C_ID_2223b33279      344         NaN           0.0   
99

In [60]:
history.apply(ref_date, axis = 1)

authorized_flag                           1
card_id                     C_ID_4e6213e9bc
city_id                                  88
category_1                                0
installments                              0
category_3                                0
merchant_category_id                     80
merchant_id                 M_ID_e020e9b302
month_lag                                -8
purchase_amount                   -0.703331
purchase_date           2017-06-25 15:33:07
category_2                                1
state_id                                 16
subsector_id                             37
purchase_amount_trim              -0.703331
purchase_year                          2017
purchase_month                            6
purchase_day                             25
purchase_hour                            15
purchase_dayofweek                        6
purchase_weekofyear                      25
purchase_weekend                          1
Name: 0, dtype: object
authorize

Name: 353, dtype: object
authorized_flag                           1
card_id                     C_ID_4e6213e9bc
city_id                                  88
category_1                                0
installments                              0
category_3                                0
merchant_category_id                     80
merchant_id                 M_ID_979ed661fc
month_lag                                -4
purchase_amount                   -0.726321
purchase_date           2017-10-11 00:57:54
category_2                                1
state_id                                 16
subsector_id                             37
purchase_amount_trim              -0.726321
purchase_year                          2017
purchase_month                           10
purchase_day                             11
purchase_hour                             0
purchase_dayofweek                        2
purchase_weekofyear                      41
purchase_weekend                          0
Name: 3

Name: 704, dtype: object
authorized_flag                           1
card_id                     C_ID_0e171c1b48
city_id                                 277
category_1                                0
installments                              0
category_3                                0
merchant_category_id                    309
merchant_id                 M_ID_5d686bfc66
month_lag                                -8
purchase_amount                   -0.716855
purchase_date           2017-06-10 11:59:31
category_2                                4
state_id                                 13
subsector_id                             21
purchase_amount_trim              -0.716855
purchase_year                          2017
purchase_month                            6
purchase_day                             10
purchase_hour                            11
purchase_dayofweek                        5
purchase_weekofyear                      23
purchase_weekend                          1
Name: 7

Name: 1014, dtype: object
authorized_flag                           1
card_id                     C_ID_fc8e41b9cf
city_id                                 170
category_1                                0
installments                              1
category_3                                1
merchant_category_id                    367
merchant_id                 M_ID_68e26f3cca
month_lag                                -4
purchase_amount                   -0.622488
purchase_date           2017-10-07 00:00:00
category_2                                3
state_id                                  8
subsector_id                             16
purchase_amount_trim              -0.622488
purchase_year                          2017
purchase_month                           10
purchase_day                              7
purchase_hour                             0
purchase_dayofweek                        5
purchase_weekofyear                      40
purchase_weekend                          1
Name: 

Name: 1356, dtype: object
authorized_flag                           1
card_id                     C_ID_4bed29d75c
city_id                                  19
category_1                                0
installments                              1
category_3                                1
merchant_category_id                    414
merchant_id                 M_ID_62ebcb8b8b
month_lag                                -4
purchase_amount                   -0.659754
purchase_date           2017-09-16 14:58:53
category_2                                1
state_id                                  9
subsector_id                             29
purchase_amount_trim              -0.659754
purchase_year                          2017
purchase_month                            9
purchase_day                             16
purchase_hour                            14
purchase_dayofweek                        5
purchase_weekofyear                      37
purchase_weekend                          1
Name: 

...

Name: 6857, dtype: object
authorized_flag                           1
card_id                     C_ID_12b7811978
city_id                                  57
category_1                                0
installments                              0
category_3                                0
merchant_category_id                    419
merchant_id                 M_ID_7d87558807
month_lag                                -1
purchase_amount                   -0.709342
purchase_date           2018-01-06 09:07:00
category_2                                5
state_id                                  5
subsector_id                              1
purchase_amount_trim              -0.709342
purchase_year                          2018
purchase_month                            1
purchase_day                              6
purchase_hour                             9
purchase_dayofweek                        5
purchase_weekofyear                       1
purchase_weekend                          1
Name: 

Name: 7233, dtype: object
authorized_flag                           1
card_id                     C_ID_25236b70f6
city_id                                  17
category_1                                0
installments                              0
category_3                                0
merchant_category_id                    683
merchant_id                 M_ID_309752ddea
month_lag                                -7
purchase_amount                   -0.677786
purchase_date           2017-07-12 21:42:46
category_2                                4
state_id                                 22
subsector_id                             34
purchase_amount_trim              -0.677786
purchase_year                          2017
purchase_month                            7
purchase_day                             12
purchase_hour                            21
purchase_dayofweek                        2
purchase_weekofyear                      28
purchase_weekend                          0
Name: 

authorized_flag                           1
card_id                     C_ID_25236b70f6
city_id                                  17
category_1                                0
installments                              0
category_3                                0
merchant_category_id                    560
merchant_id                 M_ID_c50d5d8042
month_lag                                -4
purchase_amount                   -0.735623
purchase_date           2017-10-20 21:35:33
category_2                                4
state_id                                 22
subsector_id                             34
purchase_amount_trim              -0.735623
purchase_year                          2017
purchase_month                           10
purchase_day                             20
purchase_hour                            21
purchase_dayofweek                        4
purchase_weekofyear                      42
purchase_weekend                          0
Name: 7505, dtype: object
author

Name: 7908, dtype: object
authorized_flag                           1
card_id                     C_ID_9e6b3e491a
city_id                                 116
category_1                                0
installments                              0
category_3                                0
merchant_category_id                    307
merchant_id                 M_ID_bd7c95b5f6
month_lag                               -11
purchase_amount                   -0.710844
purchase_date           2017-03-08 22:17:32
category_2                                1
state_id                                  9
subsector_id                             19
purchase_amount_trim              -0.710844
purchase_year                          2017
purchase_month                            3
purchase_day                              8
purchase_hour                            22
purchase_dayofweek                        2
purchase_weekofyear                      10
purchase_weekend                          0
Name: 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



#### history

In [19]:
aggs = {}
aggs['authorized_flag'] = [mode, 'sum', 'mean']
aggs['card_id'] = ['size']
aggs['city_id'] = [mode, 'nunique']
aggs['category_1'] = [mode, 'sum', 'mean']
aggs['installments'] = [mode, 'sum', 'mean', 'var', 'max', 'min', null_cnt]
aggs['category_3'] = [mode, 'mean']
aggs['merchant_category_id'] = [mode, 'nunique']
aggs['merchant_id'] = ['nunique']
aggs['month_lag'] = [mode, 'sum', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_amount'] = ['sum', 'mean', 'var', 'max', 'min', 'skew', over_550]
aggs['category_2'] = [mode, 'mean']
aggs['state_id'] = [mode, 'nunique']
aggs['subsector_id'] = [mode, 'nunique']
aggs['purchase_amount_trim'] = ['sum', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_year'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_month'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_day'] = [mode, 'nunique', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_hour'] = [mode, 'nunique', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_dayofweek'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_weekofyear'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_weekend'] = [mode, 'sum', 'mean']

# aggregation
history_agg = history.groupby('card_id').agg(aggs)

# change column name
history_agg.columns = pd.Index([e[0] + "_" + e[1] for e in history_agg.columns.tolist()])
history_agg.columns = ['hist_'+ c for c in history_agg.columns]

# reduce memory usage
# history_agg = reduce_mem_usage(history_agg)

In [20]:
history_agg

hist_authorized_flag_mode  hist_authorized_flag_sum  \
card_id                                                                
C_ID_058b254a5b                          1                       461   
C_ID_0d6b8c2d0f                          1                        35   
C_ID_0e171c1b48                          1                       261   
C_ID_12b7811978                          1                        36   
C_ID_190bd090c9                          1                        29   
C_ID_198914cf94                          1                       623   
C_ID_21117571cf                          1                       209   
C_ID_2223b33279                          1                        60   
C_ID_23518d5fe7                          1                       361   
C_ID_25236b70f6                          1                       528   
C_ID_3898518baa                          1                       130   
C_ID_3917d75318                          1                       239   
C_ID_3da75e85ea                          1                       791   
C_ID_3df86e0089                          1                       277   
C_ID_3fff3df454                          1                       493   
C_ID_48fb13e70f                          1                        79   
C_ID_4bed29d75c                          1                        78   
C_ID_4e6213e9bc                          1                       391   
C_ID_5037ff576e                          1                       104   
C_ID_536bff298a                          1                        34   
C_ID_55aa6d6d5e                          1                       389   
C_ID_72b66c75ad                          1                       196   
C_ID_76ac7d7a48                          1                       150   
C_ID_93d201f55f                          1                       204   
C_ID_9e6b3e491a                          1                      1272   
C_ID_a1b71153bd                          1                        38   
C_ID_a9af70f52d                          1                       201   
C_ID_ad99f08d4c                          1                       177   
C_ID_b02e55aa9d                          1                       140   
C_ID_b271e7ab60                          1                        80   
C_ID_b45d4d37b1                          1                       393   
C_ID_ca09e9cea5                          1                        41   
C_ID_d244d8976d                          1                       279   
C_ID_d3ec4a9f31                          1                        66   
C_ID_d6f97e5780                          1                       143   
C_ID_e5f5fcf6e7                          1                       223   
C_ID_fc8e41b9cf                          1                       233   

                 hist_authorized_flag_mean  hist_card_id_size  \
card_id                                                         
C_ID_058b254a5b                   0.946612                487   
C_ID_0d6b8c2d0f                   0.972222                 36   
C_ID_0e171c1b48                   0.935484                279   
C_ID_12b7811978                   0.878049                 41   
C_ID_190bd090c9                   0.828571                 35   
C_ID_198914cf94                   0.912152                683   
C_ID_21117571cf                   0.924779                226   
C_ID_2223b33279                   0.923077                 65   
C_ID_23518d5fe7                   0.932817                387   
C_ID_25236b70f6                   0.960000                550   
C_ID_3898518baa                   0.921986                141   
C_ID_3917d75318                   0.948413                252   
C_ID_3da75e85ea                   0.958788                825   
C_ID_3df86e0089                   0.945392                293   
C_ID_3fff3df454                   0.946257                521   
C_ID_48fb13e70f                   0.987500                 80   
C_ID_4bed29d75c                   0.90

#### new_history

In [63]:
aggs = {}
aggs['authorized_flag'] = [mode, 'sum', 'mean']
aggs['card_id'] = ['size']
aggs['city_id'] = [mode, 'nunique']
aggs['category_1'] = [mode, 'sum', 'mean']
aggs['installments'] = [mode, 'sum', 'mean', 'var', 'max', 'min', null_cnt]
aggs['category_3'] = [mode, 'mean']
aggs['merchant_category_id'] = [mode, 'nunique']
aggs['merchant_id'] = ['nunique']
aggs['month_lag'] = [mode, 'sum', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_amount'] = ['sum', 'mean', 'var', 'max', 'min', 'skew', over_550]
aggs['category_2'] = [mode, 'mean']
aggs['state_id'] = [mode, 'nunique']
aggs['subsector_id'] = [mode, 'nunique']
aggs['purchase_amount_trim'] = ['sum', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_year'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_month'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_day'] = [mode, 'nunique', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_hour'] = [mode, 'nunique', 'mean', 'var', 'max', 'min', 'skew']
aggs['purchase_dayofweek'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_weekofyear'] = [mode, 'nunique', 'mean', 'max', 'min']
aggs['purchase_weekend'] = [mode, 'sum', 'mean']

# aggregation
new_history_agg = new_history.groupby('card_id').agg(aggs)

# change column name
new_history_agg.columns = pd.Index([e[0] + "_" + e[1] for e in new_history_agg.columns.tolist()])
new_history_agg.columns = ['new_'+ c for c in new_history_agg.columns]

# reduce memory usage
new_history_agg = reduce_mem_usage(new_history_agg)

Mem. usage decreased to  0.10 Mb (79.8% reduction)


## 피처 사이 엔지니어링

### history & new_history

In [80]:
for df in [history, new_history]:
    for col in ['city_id', 'authorized_flag', 'category_1', 'category_2', 'category_3']:
        df[col+'_mean'] = df.groupby([col])['purchase_amount'].transform('mean')
        df[col+'_min'] = df.groupby([col])['purchase_amount'].transform('min')
        df[col+'_max'] = df.groupby([col])['purchase_amount'].transform('max')
        df[col+'_sum'] = df.groupby([col])['purchase_amount'].transform('sum')

In [81]:
history

authorized_flag          card_id  city_id  category_1  installments  \
0                   1  C_ID_4e6213e9bc       88           0           0.0   
1                   1  C_ID_4e6213e9bc       88           0           0.0   
2                   1  C_ID_4e6213e9bc       88           0           0.0   
3                   1  C_ID_4e6213e9bc       88           0           0.0   
4                   1  C_ID_4e6213e9bc       88           0           0.0   
5                   1  C_ID_4e6213e9bc      333           0           0.0   
6                   1  C_ID_4e6213e9bc       88           0           0.0   
7                   1  C_ID_4e6213e9bc        3           0           0.0   
8                   1  C_ID_4e6213e9bc       88           0           0.0   
9                   1  C_ID_4e6213e9bc       88           0           0.0   
10                  1  C_ID_4e6213e9bc       88           0           0.0   
11                  1  C_ID_4e6213e9bc       -1           0           0.0   
12                  1  C_ID_4e6213e9bc       88           0           0.0   
13                  1  C_ID_4e6213e9bc       88           0           0.0   
14                  1  C_ID_4e6213e9bc       88           0           0.0   
15                  1  C_ID_4e6213e9bc       88           0           0.0   
16                  1  C_ID_4e6213e9bc       69           0           0.0   
17                  1  C_ID_4e6213e9bc       88           0           0.0   
18                  1  C_ID_4e6213e9bc      233           0           0.0   
19                  1  C_ID_4e6213e9bc       88           0           0.0   
20                  1  C_ID_4e6213e9bc       88           0           0.0   
21                  1  C_ID_4e6213e9bc       88           0           0.0   
22                  1  C_ID_4e6213e9bc       88           0           0.0   
23                  1  C_ID_4e6213e9bc       88           0           0.0   
24                  1  C_ID_4e6213e9bc        3           0           0.0   
25                  1  C_ID_4e6213e9bc      333           0           0.0   
26                  1  C_ID_4e6213e9bc       88           0           0.0   
27                  1  C_ID_4e6213e9bc       88           0           0.0   
28                  1  C_ID_4e6213e9bc       88           0           0.0   
29                  1  C_ID_4e6213e9bc       88           0           0.0   
...               ...              ...      ...         ...           ...   
9970                0  C_ID_2223b33279      200           0           0.0   
9971                1  C_ID_2223b33279      344           0           0.0   
9972                1  C_ID_2223b33279      344           0           0.0   
9973                1  C_ID_2223b33279      344           0           0.0   
9974                1  C_ID_2223b33279      344           0           0.0   
9975                1  C_ID_2223b33279      200           0           0.0   
9976                1  C_ID_2223b33279      344           0           0.0   
9977                1  C_ID_2223b33279      107           0           0.0   
9978                1  C_ID_2223b33279      344           0           0.0   
9979                1  C_ID_2223b33279      344           0           0.0   
9980                1  C_ID_2223b33279      200           0           0.0   
9981                1  C_ID_2223b33279      344           0           0.0   
9982                0  C_ID_2223b33279      344           0           0.0   
9983                0  C_ID_2223b33279       -1           1           1.0   
9984                1  C_ID_2223b33279      344           0           0.0   
9985                1  C_ID_2223b33279      331           0           0.0   
9986                1  C_ID_2223b33279      344           0           0.0   
9987                1  C_ID_2223b33279      344           0           0.0   
9988                1  C_ID_2223b33279      344           0           0.0   
9989                1  C_ID_2223b33279      344           0           0.0   
99